In [5]:
import pandas as pd
from sklearn.decomposition import PCA
response_pca = pd.read_csv("/media/ubuntu/sda/MICrONS/response_pca.csv")

In [12]:
# 创建metadata：每300个点标记为1，其余为0
import numpy as np

# 获取数据点的总数
n_points = response_pca.shape[0]
print(f"总数据点数: {n_points}")

# 创建metadata数组
metadata = np.zeros(n_points)

# 每300个点标记为1
for i in range(0, n_points, 300):
    metadata[i] = 1

print(f"标记为1的点数: {np.sum(metadata)}")
print(f"标记为0的点数: {np.sum(metadata == 0)}")


总数据点数: 75000
标记为1的点数: 250.0
标记为0的点数: 74750


In [13]:
metadata


array([1., 0., 0., ..., 0., 0., 0.], shape=(75000,))

In [16]:
# 不进行平滑处理的分段连线3D图，标出起始点
import plotly.graph_objects as go
import numpy as np

# 创建3D图
fig = go.Figure()

# 设置每段的点数
segment_size = 250
n_points = response_pca.shape[0]
n_segments = n_points // segment_size

print(f"总数据点数: {n_points}")
print(f"每段点数: {segment_size}")
print(f"总段数: {n_segments}")

# 存储所有起始点的坐标
start_points_x = []
start_points_y = []
start_points_z = []

# 为每段创建原始连线（不进行平滑）
for i in range(n_segments):
    start_idx = i * segment_size
    end_idx = min((i + 1) * segment_size, n_points)
    
    # 获取当前段的原始数据
    segment_data = response_pca.iloc[start_idx:end_idx]
    
    # 记录起始点坐标
    start_points_x.append(segment_data.iloc[0, 0])
    start_points_y.append(segment_data.iloc[0, 1])
    start_points_z.append(segment_data.iloc[0, 2])
    
    # 添加原始连线（不进行平滑）
    fig.add_trace(go.Scatter3d(
        x=segment_data.iloc[:, 0],  
        y=segment_data.iloc[:, 1], 
        z=segment_data.iloc[:, 2],
        mode='lines+markers',
        line=dict(
            width=2,
            color=f'hsl({i * 360 / n_segments}, 70%, 50%)'  # 使用不同颜色
        ),
        marker=dict(
            size=1,
            opacity=0.6
        ),
        name=f'原始段 {i+1}',
        showlegend=True
    ))

# 添加所有起始点
fig.add_trace(go.Scatter3d(
    x=start_points_x,
    y=start_points_y,
    z=start_points_z,
    mode='markers',
    marker=dict(
        size=1,
        color='red',
        opacity=0.9,
        line=dict(
            width=2,
            color='black'
        )
    ),
    name='起始点',
    showlegend=True
))

# 设置图表布局
fig.update_layout(
    title=f'Response PCA 原始分段连线3D图（每{segment_size}个点一段，无平滑）',
    scene=dict(
        xaxis_title='PC1',
        yaxis_title='PC2',
        zaxis_title='PC3'
    ),
    width=900,
    height=700
)

fig.show()


总数据点数: 75000
每段点数: 250
总段数: 300


In [7]:
# 绘制3D散点图，使用metadata进行颜色标记
import plotly.graph_objects as go

# 创建3D散点图
fig = go.Figure()

# 添加标记为0的点（蓝色）
mask_0 = metadata == 0
fig.add_trace(go.Scatter3d(
    x=response_pca.iloc[mask_0, 0],  
    y=response_pca.iloc[mask_0, 1], 
    z=response_pca.iloc[mask_0, 2],
    mode='markers',
    marker=dict(
        size=0.5,
        color='blue',
        opacity=0.6
    ),
    name='标记为0的点',
    showlegend=True
))

# 添加标记为1的点（红色）
mask_1 = metadata == 1
fig.add_trace(go.Scatter3d(
    x=response_pca.iloc[mask_1, 0],  
    y=response_pca.iloc[mask_1, 1], 
    z=response_pca.iloc[mask_1, 2],
    mode='markers',
    marker=dict(
        size=1,
        color='red',
        opacity=0.8
    ),
    name='标记为1的点',
    showlegend=True
))

# 设置图表布局
fig.update_layout(
    title='Response PCA 3D散点图（每300个点标记为1）',
    scene=dict(
        xaxis_title='PC1',
        yaxis_title='PC2',
        zaxis_title='PC3'
    ),
    width=800,
    height=600
)

fig.show()


In [14]:
# 对每250个点的线段进行高斯平滑处理，并标出起始点
import plotly.graph_objects as go
from scipy import ndimage
import numpy as np

def gaussian_smooth_segment(data, sigma=1.0):
    """
    对数据段进行高斯平滑
    data: 输入数据 (n_points, n_features)
    sigma: 高斯核的标准差
    """
    smoothed_data = np.zeros_like(data)
    for i in range(data.shape[1]):  # 对每个特征分别平滑
        smoothed_data[:, i] = ndimage.gaussian_filter1d(data[:, i], sigma=sigma)
    return smoothed_data

# 创建3D图
fig = go.Figure()

# 设置每段的点数和平滑参数
segment_size = 250
sigma = 2.0  # 高斯平滑的标准差，可以调整
n_points = response_pca.shape[0]
n_segments = n_points // segment_size

print(f"总数据点数: {n_points}")
print(f"每段点数: {segment_size}")
print(f"总段数: {n_segments}")
print(f"高斯平滑标准差: {sigma}")

# 存储所有起始点的坐标
start_points_x = []
start_points_y = []
start_points_z = []

# 为每段创建平滑后的连线
for i in range(n_segments):
    start_idx = i * segment_size
    end_idx = min((i + 1) * segment_size, n_points)
    
    # 获取当前段的原始数据
    segment_data = response_pca.iloc[start_idx:end_idx]
    
    # 对当前段进行高斯平滑
    smoothed_data = gaussian_smooth_segment(segment_data.values, sigma=sigma)
    
    # 记录起始点坐标
    start_points_x.append(smoothed_data[0, 0])
    start_points_y.append(smoothed_data[0, 1])
    start_points_z.append(smoothed_data[0, 2])
    
    # 添加平滑后的连线
    fig.add_trace(go.Scatter3d(
        x=smoothed_data[:, 0],  
        y=smoothed_data[:, 1], 
        z=smoothed_data[:, 2],
        mode='lines+markers',
        line=dict(
            width=3,
            color=f'hsl({i * 360 / n_segments}, 70%, 50%)'  # 使用不同颜色
        ),
        marker=dict(
            size=1.5,
            opacity=0.8
        ),
        name=f'平滑段 {i+1}',
        showlegend=True
    ))

# 添加所有起始点
fig.add_trace(go.Scatter3d(
    x=start_points_x,
    y=start_points_y,
    z=start_points_z,
    mode='markers',
    marker=dict(
        size=1,
        color='red',
        opacity=0.9,
        line=dict(
            width=2,
            color='black'
        )
    ),
    name='起始点',
    showlegend=True
))

# 设置图表布局
fig.update_layout(
    title=f'Response PCA 高斯平滑分段连线3D图（每{segment_size}个点一段，σ={sigma}）',
    scene=dict(
        xaxis_title='PC1',
        yaxis_title='PC2',
        zaxis_title='PC3'
    ),
    width=900,
    height=700
)

fig.show()


总数据点数: 75000
每段点数: 250
总段数: 300
高斯平滑标准差: 2.0
